In [54]:
import pandas as pd
embed=0

if embed==1:

    # Load Lending Club Loan Data
    loan_data = pd.read_csv('loan.csv')

    # Basic preprocessing
    loan_data = loan_data[['loan_amnt', 'term', 'int_rate', 'grade', 'emp_length', 'home_ownership', 'annual_inc', 'purpose', 'addr_state', 'loan_status', 'desc']]
    loan_data.dropna(inplace=True)

    loan_data=loan_data[~(loan_data['desc'].str.strip()=='')]
    #loan_data.shape

    #CLEAN LOAN DATA
    loan_data['desc_clean'] = loan_data['desc'].apply(lambda x: x.lower().replace('\n', ' ').strip())
    loan_data=loan_data.sample(n=15000, random_state=42)
else:
    loan_data = pd.read_pickle("loan_data_with_embeddings.pkl")

In [72]:
loan_data.columns

Index(['loan_amnt', 'term', 'int_rate', 'grade', 'emp_length',
       'home_ownership', 'annual_inc', 'purpose', 'addr_state', 'loan_status',
       'desc', 'desc_clean', 'desc_embeddings', 'risk_prediction',
       'combined_text'],
      dtype='object')

In [73]:
loan_data.head()

loan_amnt  term  int_rate  grade  emp_length  home_ownership  \
1805711       9600     0     14.33      2           2               4   
2119945       9875     0      7.29      0           4               4   
1738521      21000     0      7.90      0           3               0   
1822358      25000     1     19.72      3           1               0   
2101985      15850     1     13.49      2           1               0   

         annual_inc  purpose  addr_state  loan_status  \
1805711     40000.0        2          30  Charged Off   
2119945     30000.0        2           6   Fully Paid   
1738521    125000.0        2           4   Fully Paid   
1822358     94000.0        2          44   Fully Paid   
2101985     36000.0        2           1   Fully Paid   

                                                      desc  \
1805711    Borrower added on 01/11/13 > I am opening a ...   
2119945    Borrower added on 01/21/11 > I have 3 high i...   
1738521    Borrower added on 08/02/13 > Hi. I am consol...   
1822358    Borrower added on 10/24/12 > Debt cosolidati...   
2101985    Borrower added on 11/26/11 > I am trying to ...   

                                                desc_clean  \
1805711  borrower added on 01/11/13 > i am opening a bu...   
2119945  borrower added on 01/21/11 > i have 3 high int...   
1738521  borrower added on 08/02/13 > hi. i am consolid...   
1822358  borrower added on 10/24/12 > debt cosolidation...   
2101985  borrower added on 11/26/11 > i am trying to co...   

                                           desc_embeddings  risk_prediction  \
1805711  [0.009529114, -0.0692749, -0.010536194, -0.011...                0   
2119945  [0.017105103, -0.023284912, 0.0042762756, 0.01...                1   
1738521  [0.047332764, -0.008430481, -0.011184692, -0.0...                1   
1822358  [0.038391113, 0.014656067, -0.021316528, 0.054...                1   
2101985  [0.0047302246, -0.017990112, 0.0052871704, 0.0...                1   

                                             combined_text  
1805711  addr_state: 30 annual_inc: 40000.0 desc:   Bor...  
2119945  addr_state: 6 annual_inc: 30000.0 desc:   Borr...  
1738521  addr_state: 4 annual_inc: 125000.0 desc:   Bor...  
1822358  addr_state: 44 annual_inc: 94000.0 desc:   Bor...  
2101985  addr_state: 1 annual_inc: 36000.0 desc:   Borr...

## Metadata dictionary

In [55]:
metadata_dict = pd.read_excel('LCDataDictionary.xlsx', sheet_name=None)

# Display metadata dictionary to understand dataset columns
for sheet in metadata_dict:
    print(f"Sheet: {sheet}")
    display(metadata_dict[sheet].head())


Sheet: LoanStats


LoanStatNew                                        Description
0        acc_now_delinq  The number of accounts on which the borrower i...
1  acc_open_past_24mths         Number of trades opened in past 24 months.
2            addr_state  The state provided by the borrower in the loan...
3              all_util              Balance to credit limit on all trades
4            annual_inc  The self-reported annual income provided by th...

Sheet: browseNotes


BrowseNotesFile                                        Description
0            acceptD    The date which the borrower accepted  the offer
1       accNowDelinq  The number of accounts on which the borrower i...
2  accOpenPast24Mths         Number of trades opened in past 24 months.
3          addrState  The state provided by the borrower in the loan...
4           all_util              Balance to credit limit on all trades

Sheet: RejectStats


RejectStats File                                        Description
0      Amount Requested         The total amount requested by the borrower
1      Application Date               The date which the borrower applied 
2            Loan Title            The loan title provided by the borrower
3            Risk_Score  For applications prior to November 5, 2013 the...
4  Debt-To-Income Ratio  A ratio calculated using the borrower’s total ...

## Using Cohere to create vector embeddings

In [56]:
import cohere
#from ratelimit import limits, sleep_and_retry
co = cohere.Client('')

embed=0

if embed==1: #embed and write
    # Initialize Cohere client
    # Generate vector embeddings for loan descriptions
    embeddings_response = co.embed(texts=loan_data['desc_clean'].tolist(), model='embed-english-light-v3.0', input_type="search_query")
    loan_data['desc_embeddings'] = embeddings_response.embeddings
    loan_data.to_pickle("loan_data_with_embeddings.pkl")

elif embed==2: #only write
    loan_data.to_pickle("loan_data_with_embeddings.pkl")
    
else:   #read data
    loan_data = pd.read_pickle("loan_data_with_embeddings.pkl")

In [57]:
loan_data.head()

loan_amnt        term  int_rate grade emp_length home_ownership  \
1805711       9600   36 months     14.33     C    2 years           RENT   
2119945       9875   36 months      7.29     A    4 years           RENT   
1738521      21000   36 months      7.90     A    3 years       MORTGAGE   
1822358      25000   60 months     19.72     D  10+ years       MORTGAGE   
2101985      15850   60 months     13.49     C  10+ years       MORTGAGE   

         annual_inc             purpose addr_state  loan_status  \
1805711     40000.0  debt_consolidation         NV  Charged Off   
2119945     30000.0  debt_consolidation         CT   Fully Paid   
1738521    125000.0  debt_consolidation         CA   Fully Paid   
1822358     94000.0  debt_consolidation         WA   Fully Paid   
2101985     36000.0  debt_consolidation         AL   Fully Paid   

                                                      desc  \
1805711    Borrower added on 01/11/13 > I am opening a ...   
2119945    Borrower added on 01/21/11 > I have 3 high i...   
1738521    Borrower added on 08/02/13 > Hi. I am consol...   
1822358    Borrower added on 10/24/12 > Debt cosolidati...   
2101985    Borrower added on 11/26/11 > I am trying to ...   

                                                desc_clean  \
1805711  borrower added on 01/11/13 > i am opening a bu...   
2119945  borrower added on 01/21/11 > i have 3 high int...   
1738521  borrower added on 08/02/13 > hi. i am consolid...   
1822358  borrower added on 10/24/12 > debt cosolidation...   
2101985  borrower added on 11/26/11 > i am trying to co...   

                                           desc_embeddings  
1805711  [0.009529114, -0.0692749, -0.010536194, -0.011...  
2119945  [0.017105103, -0.023284912, 0.0042762756, 0.01...  
1738521  [0.047332764, -0.008430481, -0.011184692, -0.0...  
1822358  [0.038391113, 0.014656067, -0.021316528, 0.054...  
2101985  [0.0047302246, -0.017990112, 0.0052871704, 0.0...

## Classification Model

In [61]:
import pickle
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.preprocessing import LabelEncoder

# Encode categorical variables
label_encoders = {}
for column in ['term', 'grade', 'emp_length', 'home_ownership', 'purpose', 'addr_state']:
    le = LabelEncoder()
    loan_data[column] = le.fit_transform(loan_data[column])
    label_encoders[column] = le

# Prepare features and target
X = loan_data[['loan_amnt', 'term', 'int_rate', 'grade', 'emp_length', 'home_ownership', 'annual_inc', 'purpose', 'addr_state']]
y = loan_data['loan_status'].apply(lambda x: 1 if x == 'Fully Paid' else 0)

# Train-test split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Train RandomForest model
model = RandomForestClassifier()
model.fit(X_train, y_train)

# Evaluate model
from sklearn.metrics import accuracy_score
predictions = model.predict(X_test)
print(f"Model Accuracy: {accuracy_score(y_test, predictions)}")

loan_data['risk_prediction'] = model.predict(loan_data[['loan_amnt', 'term', 'int_rate', 'grade', 'emp_length', 'home_ownership', 'annual_inc', 'purpose', 'addr_state']])

# Save the trained model
with open("loan_risk_model.pkl", "wb") as f:
    pickle.dump(model, f)

loan_data.to_pickle("loan_data_with_predictions.pkl")

Model Accuracy: 0.8266666666666667


In [62]:
# Load the trained model
with open("loan_risk_model.pkl", "rb") as f:
    model = pickle.load(f)

In [63]:
with open("label_encoders.pkl", "wb") as f:
    pickle.dump(label_encoders, f)

# Create Labelled dataset for Cohere's classification algorithm

In [64]:
from cohere import ClassifyExample

# Load the dataset with predictions
loan_data = pd.read_pickle("loan_data_with_predictions.pkl")


# Define a function to concatenate all column headers and values
def concatenate_columns(row):
    columns_to_include = loan_data.columns.difference(['desc_clean', 'desc_embeddings', 'risk_prediction'])
    concatenated_text = ' '.join(f"{col}: {row[col]}" for col in columns_to_include)
    return concatenated_text

# Apply the function to create a new column with concatenated text
loan_data['combined_text'] = loan_data.apply(concatenate_columns, axis=1)

In [65]:
# Apply the function to create a new column with concatenated text
loan_data.head()

loan_amnt  term  int_rate  grade  emp_length  home_ownership  \
1805711       9600     0     14.33      2           2               4   
2119945       9875     0      7.29      0           4               4   
1738521      21000     0      7.90      0           3               0   
1822358      25000     1     19.72      3           1               0   
2101985      15850     1     13.49      2           1               0   

         annual_inc  purpose  addr_state  loan_status  \
1805711     40000.0        2          30  Charged Off   
2119945     30000.0        2           6   Fully Paid   
1738521    125000.0        2           4   Fully Paid   
1822358     94000.0        2          44   Fully Paid   
2101985     36000.0        2           1   Fully Paid   

                                                      desc  \
1805711    Borrower added on 01/11/13 > I am opening a ...   
2119945    Borrower added on 01/21/11 > I have 3 high i...   
1738521    Borrower added on 08/02/13 > Hi. I am consol...   
1822358    Borrower added on 10/24/12 > Debt cosolidati...   
2101985    Borrower added on 11/26/11 > I am trying to ...   

                                                desc_clean  \
1805711  borrower added on 01/11/13 > i am opening a bu...   
2119945  borrower added on 01/21/11 > i have 3 high int...   
1738521  borrower added on 08/02/13 > hi. i am consolid...   
1822358  borrower added on 10/24/12 > debt cosolidation...   
2101985  borrower added on 11/26/11 > i am trying to co...   

                                           desc_embeddings  risk_prediction  \
1805711  [0.009529114, -0.0692749, -0.010536194, -0.011...                0   
2119945  [0.017105103, -0.023284912, 0.0042762756, 0.01...                1   
1738521  [0.047332764, -0.008430481, -0.011184692, -0.0...                1   
1822358  [0.038391113, 0.014656067, -0.021316528, 0.054...                1   
2101985  [0.0047302246, -0.017990112, 0.0052871704, 0.0...                1   

                                             combined_text  
1805711  addr_state: 30 annual_inc: 40000.0 desc:   Bor...  
2119945  addr_state: 6 annual_inc: 30000.0 desc:   Borr...  
1738521  addr_state: 4 annual_inc: 125000.0 desc:   Bor...  
1822358  addr_state: 44 annual_inc: 94000.0 desc:   Bor...  
2101985  addr_state: 1 annual_inc: 36000.0 desc:   Borr...

In [66]:
# Get the top 45 high-risk and top 45 low-risk samples
high_risk_samples = loan_data[loan_data['risk_prediction'] == 0].sample(n=45)
low_risk_samples = loan_data[loan_data['risk_prediction'] == 1].sample(n=45)

# Combine the samples and create the labelled dataset
labelled_dataset = []
for _, row in high_risk_samples.iterrows():
    labelled_dataset.append(ClassifyExample(text=row['combined_text'], label="High Risk"))
for _, row in low_risk_samples.iterrows():
    labelled_dataset.append(ClassifyExample(text=row['combined_text'], label="Low Risk"))

# Save the labelled dataset to a pickle file
with open("labelled_dataset.pkl", "wb") as f:
    pickle.dump(labelled_dataset, f)

In [67]:
labelled_dataset

[ClassifyExample(text='addr_state: 4 annual_inc: 52000.0 desc:   Borrower added on 05/09/12 > I plan to use the proceeds to consolidate my debt.  I have a very secure job in government and the payment required is more than affordable.<br> emp_length: 10 grade: 4 home_ownership: 4 int_rate: 20.5 loan_amnt: 24000 loan_status: Charged Off purpose: 2 risk_prediction: 0 term: 0', label='High Risk'),
 ClassifyExample(text='addr_state: 9 annual_inc: 45000.0 desc:   Borrower added on 06/26/12 > To consolidate all my debts and have only one payment to make<br> emp_length: 5 grade: 1 home_ownership: 4 int_rate: 12.12 loan_amnt: 12000 loan_status: Charged Off purpose: 2 risk_prediction: 0 term: 0', label='High Risk'),
 ClassifyExample(text='addr_state: 32 annual_inc: 103950.0 desc: I will be using the loan to consolidate all of my credit cards into one payment.  I make all of my credit card payments on time and always pay more than the minimum, but they have all raised their interest rates to the

## LANGCHAIN AND RAG

In [23]:
import fitz  # PyMuPDF
import requests
from bs4 import BeautifulSoup
from langchain.docstore.document import Document

# Function to parse PDF files
def parse_pdf(file_path):
    doc = fitz.open(file_path)
    text = ""
    for page in doc:
        text += page.get_text()
    return text

# Function to parse website content
def parse_website(url):
    response = requests.get(url)
    soup = BeautifulSoup(response.text, 'html.parser')
    return soup.get_text()

# Chunking function
def chunk_text(text, chunk_size=500):
    words = text.split()
    chunks = [' '.join(words[i:i + chunk_size]) for i in range(0, len(words), chunk_size)]
    return chunks

In [24]:
# Function to parse website content

# Example of loading and parsing PDFs
pdf_files = ['regulations/hmda.pdf', 'regulations/udaap.pdf', 'regulations/tila.pdf', 'regulations/fcra.pdf', 'regulations/fllr.pdf']
regulations_from_pdfs = [parse_pdf(file) for file in pdf_files]
#chunked_regulations_from_pdfs = [chunk for doc in regulations_from_pdfs for chunk in chunk_text(doc)]

# Example of loading and parsing websites
website_urls = ['https://richeymay.com/resource/articles/regulatory-compliance-mortgage-lenders/', 'https://www.ncontracts.com/nsight-blog/what-is-regulatory-compliance-for-banks', ]
regulations_from_websites = [parse_website(url) for url in website_urls]
#chunked_regulations_from_websites = [chunk for doc in regulations_from_websites for chunk in chunk_text(doc)]

# Combine all regulations
all_regulations = regulations_from_pdfs + regulations_from_websites

In [25]:
all_regulations

[' \n \n \n \n1 \nEXECUTIVE SUMMARY OF THE 2020 HOME MORTGAGE DISCLOSURE ACT (REGULATION C) FINAL RULE \n1700 G Street NW, Washington, DC 20552                                                           \n \n \nThis Executive Summary of the 2020 Home Mortgage Disclosure Act (Regulation C) \nFinal Rule was published on April 16, 2020, and has not been updated to reflect the \n2022 date.  On December 6, 2022, the Bureau issued a blog post to address questions \nregarding the NCRC Order: https://www.consumerfinance.gov/about-us/blog/changes-\nto-hmda-closed-end-loan-reporting-threshold/. \nApril 16, 2020 \n \n \nExecutive Summary of the 2020 Home \nMortgage Disclosure Act (Regulation C) Final \nRule1  \nOn April 16, 2020, the Consumer Financial Protection Bureau (Bureau) issued a final rule \namending Regulation C.  This final rule adjusts Regulation C’s institutional and transactional \ncoverage thresholds for closed-end mortgage loans and open-end lines of credit.  Effective July 1, \n20

In [26]:
# Chunk text using RecursiveCharacterTextSplitter
from langchain.text_splitter import RecursiveCharacterTextSplitter

text_splitter = RecursiveCharacterTextSplitter(chunk_size=2048, chunk_overlap=256)
docs = text_splitter.create_documents(all_regulations)

### Load the regulations vector store

In [27]:
# import faiss
# from langchain_community.vectorstores import FAISS
# from langchain.docstore.in_memory import InMemoryDocstore
# from langchain.docstore.document import Document
# from langchain.embeddings.cohere import CohereEmbeddings
# import numpy as np

# co = cohere.Client('')

# # Combine loan descriptions and regulations
# # combined_texts = loan_data['desc_clean'].tolist() + all_regulations
# # combined_metadata = [{"type": "loan", "loan_id": idx} for idx in loan_data.index] + [{"type": "regulation", "reg_id": idx} for idx in range(len(all_regulations))]



# # # Generate embeddings for combined data
# # combined_embeddings_response = co.embed(texts=combined_texts,model='embed-english-light-v3.0', input_type="search_query")
# # combined_embeddings = combined_embeddings_response.embeddings

# # # Convert embeddings to numpy array
# # combined_embeddings_array = np.array(combined_embeddings, dtype=np.float32)
# # dimension = combined_embeddings_array.shape[1]

# # # Initialize FAISS index
# # index = faiss.IndexFlatL2(dimension)
# # index.add(combined_embeddings_array)

In [28]:
# # Generate embeddings for regulatory documents
# reg_embeddings_response = co.embed(
#     texts=all_regulations,
#     model='embed-english-light-v3.0', input_type="search_query"
# )
# reg_embeddings = reg_embeddings_response.embeddings

# # Convert embeddings to numpy array
# reg_embeddings_array = np.array(reg_embeddings, dtype=np.float32)
# dimension = reg_embeddings_array.shape[1]

# # Initialize FAISS index
# index = faiss.IndexFlatL2(dimension)
# index.add(reg_embeddings_array)

# # Prepare documents
# documents = [Document(page_content=text, metadata={"type": "regulation", "reg_id": idx}) for idx, text in enumerate(all_regulations)]
# docstore = InMemoryDocstore(documents)

# # Initialize Cohere embeddings
# embedding_function = CohereEmbeddings(cohere_api_key="",  model='embed-english-light-v3.0')

# # Create FAISS vector store
# faiss_store = FAISS(embedding_function=embedding_function, index=index, docstore=docstore, index_to_docstore_id={i: str(i) for i in range(len(documents))})

# # Save the FAISS index and metadata
# faiss.write_index(index, "regulations_faiss_index.bin")
# with open("regulations_metadata.pkl", "wb") as f:
#     pickle.dump({"documents": documents, "index_to_docstore_id": {i: str(i) for i in range(len(documents))}}, f)

In [29]:
# # Prepare documents
# documents = [Document(page_content=text, metadata=meta) for text, meta in zip(combined_texts, combined_metadata)]
# docstore = InMemoryDocstore(documents)

# # Initialize Cohere embeddings
# embedding_function = CohereEmbeddings(cohere_api_key="")

# # Create FAISS vector store
# faiss_store = FAISS(embedding_function=embedding_function, index=index, docstore=docstore, index_to_docstore_id={i: str(i) for i in range(len(documents))})

# # Save the FAISS index and metadata
# faiss.write_index(index, "combined_faiss_index.bin")
# with open("combined_metadata.pkl", "wb") as f:
#     pickle.dump({"documents": documents, "index_to_docstore_id": {i: str(i) for i in range(len(documents))}}, f)

In [30]:
# # Load the FAISS index
# index = faiss.read_index("combined_faiss_index.bin")

# # Load the metadata
# with open("combined_metadata.pkl", "rb") as f:
#     metadata = pickle.load(f)

# documents = metadata["documents"]
# index_to_docstore_id = metadata["index_to_docstore_id"]
# docstore = InMemoryDocstore(documents)

# # Create FAISS vector store
# faiss_store = FAISS(embedding_function=embedding_function, index=index, docstore=docstore, index_to_docstore_id=index_to_docstore_id)

In [31]:
from langchain_community.vectorstores import FAISS

import cohere
from langchain.embeddings.cohere import CohereEmbeddings
from langchain.vectorstores import FAISS

# Initialize Cohere client
co = cohere.Client('')

# Initialize Cohere embeddings
cohere_embeddings = CohereEmbeddings(model='embed-english-light-v3.0', cohere_api_key="")

# Create FAISS vector store from documents
vectorstore_faiss = FAISS.from_documents(docs, cohere_embeddings)


c:\Users\Harsh Vora\AppData\Local\Programs\Python\Python310\lib\site-packages\langchain_core\_api\deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.cohere.CohereEmbeddings` was deprecated in langchain-community 0.0.30 and will be removed in 0.2.0. An updated version of the class exists in the langchain-cohere package and should be used instead. To use it run `pip install -U langchain-cohere` and import as `from langchain_cohere import CohereEmbeddings`.
  warn_deprecated(


In [32]:
vectorstore_faiss.save_local("faiss_index")

In [33]:
import pickle

# Save the FAISS index and metadata
vectorstore_faiss.save_local("regulations_faiss")
with open("regulations_metadata.pkl", "wb") as f:
    pickle.dump({"documents": docs, "index_to_docstore_id": vectorstore_faiss.index_to_docstore_id}, f)

# TESTING

In [34]:
loan_data.index

Index([1805711, 2119945, 1738521, 1822358, 2101985, 1780688, 2140836, 1740262,
       1831575, 1789860,
       ...
       1744405, 2116348, 1856820, 1858765, 1741591, 1769627, 2087250, 2122156,
       1793666, 1859025],
      dtype='int64', length=15000)

In [35]:
loan_id=1805711
loan_info = loan_data.loc[loan_id]

In [36]:
import numpy as np

In [37]:
loan_desc_embedding = np.array(loan_info['desc_embeddings'], dtype=np.float32)

In [38]:
loan_info.desc

'  Borrower added on 01/11/13 > I am opening a business. This loan which easily i can pay off will help me to pay he small loans on my other accounts, doing so it will prepare me for a higher credit line for my business.<br>'

In [39]:
loan_desc_embedding

array([ 0.00952911, -0.0692749 , -0.01053619, -0.01197052, -0.01809692,
       -0.0335083 ,  0.01712036,  0.00419998,  0.03839111, -0.0058403 ,
        0.05010986,  0.10168457, -0.02125549, -0.07965088,  0.00353813,
        0.06610107,  0.03408813,  0.03062439, -0.04598999,  0.00247383,
       -0.08001709, -0.00166512, -0.02748108, -0.06738281,  0.04223633,
        0.01078033, -0.02661133,  0.01359558, -0.03475952,  0.04229736,
       -0.00893402, -0.02645874,  0.09967041,  0.06561279,  0.02178955,
        0.02206421, -0.03909302, -0.03683472,  0.04656982, -0.03256226,
        0.03103638, -0.08557129,  0.05587769,  0.03775024,  0.05392456,
       -0.00342941,  0.09210205,  0.01000214,  0.05178833, -0.04827881,
        0.04187012,  0.00289536,  0.03179932,  0.00206757,  0.04174805,
        0.03182983, -0.03759766,  0.08105469, -0.00292397, -0.03884888,
       -0.0340271 , -0.00525284, -0.02377319, -0.03555298, -0.03167725,
        0.00581741, -0.03509521, -0.02598572, -0.02345276, -0.04

In [40]:
def get_embedding(text):
    response = co.embed(texts=[text], model='embed-english-light-v3.0', input_type="search_query")
    return response.embeddings[0]

In [41]:
# from langchain import Chain

# # Function to perform FAISS search
# def search_faiss(input_vector, k=5):
#     distances, indices = index.search(np.array([input_vector]), k)
#     return indices[0]

In [42]:
similar_regs=vectorstore_faiss.search(loan_info['desc_clean'], k=5, search_type="similarity")

In [43]:
similar_regs

[Document(page_content='(1)\t In general. Any person who makes or arranges loans and who uses \na consumer credit score, as defined in subsection (f), in connection \nwith an application initiated or sought by a consumer for a closed end \n§\xa0609 - 15 U.S.C. §\xa01681g\n55\nloan or the establishment of an open end loan for a consumer purpose \nthat is secured by 1 to 4 units of residential real property (hereafter in \nthis subsection referred to as the “lender”) shall provide the following \nto the consumer as soon as reasonably practicable:\n(A)\t Information Required under Subsection (f)\n(i)\t\nIn general. A copy of the information identified in \nsubsection (f) that was obtained from a consumer \nreporting agency or was developed and used by the user \nof the information.\n(ii)\t Notice under subparagraph (D). In addition to the \ninformation provided to it by a third party that provided \nthe credit score or scores, a lender is only required to \nprovide the notice contained in

In [44]:
# Load the metadata for regulations
with open("regulations_metadata.pkl", "rb") as f:
    metadata = pickle.load(f)

documents = metadata["documents"]

In [45]:
documents

[Document(page_content='1 \nEXECUTIVE SUMMARY OF THE 2020 HOME MORTGAGE DISCLOSURE ACT (REGULATION C) FINAL RULE \n1700 G Street NW, Washington, DC 20552                                                           \n \n \nThis Executive Summary of the 2020 Home Mortgage Disclosure Act (Regulation C) \nFinal Rule was published on April 16, 2020, and has not been updated to reflect the \n2022 date.  On December 6, 2022, the Bureau issued a blog post to address questions \nregarding the NCRC Order: https://www.consumerfinance.gov/about-us/blog/changes-\nto-hmda-closed-end-loan-reporting-threshold/. \nApril 16, 2020 \n \n \nExecutive Summary of the 2020 Home \nMortgage Disclosure Act (Regulation C) Final \nRule1  \nOn April 16, 2020, the Consumer Financial Protection Bureau (Bureau) issued a final rule \namending Regulation C.  This final rule adjusts Regulation C’s institutional and transactional \ncoverage thresholds for closed-end mortgage loans and open-end lines of credit.  Effective Ju

In [46]:
#compliance_results = [documents[int(reg[0].doc_id)].page_content for reg in similar_regs]

relevant_text=[reg.page_content for reg in similar_regs]
relevant_text


['(1)\t In general. Any person who makes or arranges loans and who uses \na consumer credit score, as defined in subsection (f), in connection \nwith an application initiated or sought by a consumer for a closed end \n§\xa0609 - 15 U.S.C. §\xa01681g\n55\nloan or the establishment of an open end loan for a consumer purpose \nthat is secured by 1 to 4 units of residential real property (hereafter in \nthis subsection referred to as the “lender”) shall provide the following \nto the consumer as soon as reasonably practicable:\n(A)\t Information Required under Subsection (f)\n(i)\t\nIn general. A copy of the information identified in \nsubsection (f) that was obtained from a consumer \nreporting agency or was developed and used by the user \nof the information.\n(ii)\t Notice under subparagraph (D). In addition to the \ninformation provided to it by a third party that provided \nthe credit score or scores, a lender is only required to \nprovide the notice contained in subparagraph (D).\n(B

In [47]:
response_text = "\n\n".join(relevant_text)
cohere_response = co.chat(
    message=f"Based on the following regulatory comments, compare the loan comments: {loan_info.desc} with some regulations that may be relevant: {response_text} and provide a compliance risk assessment for the loan",
    max_tokens=150,
    connectors=[{"id": "web-search"}]
)

In [48]:
cohere_response

NonStreamedChatResponse(text="The borrower's comment indicates a desire to consolidate their existing small loans into one larger loan, which they believe will improve their creditworthiness and help them secure a higher credit line for their business. This is a common strategy for borrowers who want to simplify their debt obligations and potentially reduce their overall interest costs.\n\nOn the other hand, the provided regulations seem to be focused on consumer protection and disclosure requirements related to loans, particularly those involving residential real estate and consumer credit scores. The regulations outline the information that lenders are required to provide to consumers, including credit scores, key factors, and associated disclosures.\n\nBoth the comment and the regulations touch on loans, but from different perspectives. The borrower is concerned with their personal financial strategy, while the regulations", generation_id='97e98497-e64e-465b-8da6-3aa96f72fd80', cita

In [49]:
cohere_response.text

"The borrower's comment indicates a desire to consolidate their existing small loans into one larger loan, which they believe will improve their creditworthiness and help them secure a higher credit line for their business. This is a common strategy for borrowers who want to simplify their debt obligations and potentially reduce their overall interest costs.\n\nOn the other hand, the provided regulations seem to be focused on consumer protection and disclosure requirements related to loans, particularly those involving residential real estate and consumer credit scores. The regulations outline the information that lenders are required to provide to consumers, including credit scores, key factors, and associated disclosures.\n\nBoth the comment and the regulations touch on loans, but from different perspectives. The borrower is concerned with their personal financial strategy, while the regulations"

In [68]:
loan_info

loan_amnt                                                       9600
term                                                               0
int_rate                                                       14.33
grade                                                              2
emp_length                                                         2
home_ownership                                                     4
annual_inc                                                   40000.0
purpose                                                            2
addr_state                                                        30
loan_status                                              Charged Off
desc                 Borrower added on 01/11/13 > I am opening a ...
desc_clean         borrower added on 01/11/13 > i am opening a bu...
desc_embeddings    [0.009529114, -0.0692749, -0.010536194, -0.011...
risk_prediction                                                    0
Name: 1805711, dtype: object

In [69]:
combined_text = ' '.join(f"{col}: {loan_info[col]}" for col in loan_data.columns.difference(['desc_clean', 'desc_embeddings', 'risk_prediction', 'combined_text']))

In [70]:
combined_text

'addr_state: 30 annual_inc: 40000.0 desc:   Borrower added on 01/11/13 > I am opening a business. This loan which easily i can pay off will help me to pay he small loans on my other accounts, doing so it will prepare me for a higher credit line for my business.<br> emp_length: 2 grade: 2 home_ownership: 4 int_rate: 14.33 loan_amnt: 9600 loan_status: Charged Off purpose: 2 term: 0'

In [71]:
loan_data.columns

Index(['loan_amnt', 'term', 'int_rate', 'grade', 'emp_length',
       'home_ownership', 'annual_inc', 'purpose', 'addr_state', 'loan_status',
       'desc', 'desc_clean', 'desc_embeddings', 'risk_prediction',
       'combined_text'],
      dtype='object')